In [1]:
import glob
import numpy as np
import pandas as pd
from scipy import stats
from scipy.stats import shapiro
from scipy.special import boxcox1p
import matplotlib.pyplot as plt
pd.options.display.max_columns=None
import seaborn as sns

# Extracting Features for departments:

In [91]:
terridata_tabs_dpto_only = []
for i in range(len(terridata_tabs)):
    terridata_tabs_dpto_only.append(terridata_tabs[i][terridata_tabs[i]['codigo_entidad'].isin(list(df_vars_modeling['codigo_departamento']*1000)+[11001])])

In [92]:
terridata_tabs_dpto_only[13][terridata_tabs_dpto_only[13]['codigo_entidad']==1001]

Empty DataFrame
Columns: [codigo_departamento, departamento, codigo_entidad, entidad, dimension, subcategoria, indicador, dato_numerico, dato_cualitativo, anio, mes, fuente, unidad_de_medida]
Index: []

In [93]:
def select_features_dpto(df):
    selected_df_features = []
    for indicador in list(df['indicador'].unique()):
        if len(df[df['indicador']==indicador]['anio'].unique()) > 2 and len(df[df['indicador']==indicador]) > 30:
            selected_df_features.append(indicador)
    return selected_df_features

In [94]:
# We select features based on data completion (by year and municipality):
selected_features_dpto = []
for i in range(len(terridata_tabs_dpto_only)):
    selected_features_dpto.append(select_features_dpto(terridata_tabs_dpto_only[i]))
    print(terridata_tabs_dpto_only[i]['dimension'].unique()[0],len(selected_features_dpto[i]))

economia 44
ambiente 0
percepcion_ciudadana 0
justicia_y_derecho 55
educacion 19
presupuesto_general_de_la_nacion 0
demografia_y_poblacion 0
descripcion_general 0
vivienda_y_acceso_a_servicios_publicos 3
conflicto_armado_y_seguridad_ciudadana 1
salud 19
finanzas_publicas 50
censo_2005_y_proyecciones_dane 124
medicion_de_desempenio_municipal 3
mercado_laboral 0
seguridad_integral_maritima_y_fluvial 45
pobreza 3
ordenamiento_territorial 0


In [95]:
filtered_tabs_dpto_only = []
for i in range(len(terridata_tabs_dpto_only)):
    filtered_tabs_dpto_only.append(terridata_tabs_dpto_only[i][terridata_tabs_dpto_only[i]['indicador'].isin(selected_features_dpto[i])])

# MDM

In [96]:
df_vars_modeling_dpto = pd.pivot(filtered_tabs_dpto_only[13], index=['anio', 'codigo_departamento', 'codigo_entidad'], columns='indicador', values='dato_numerico').reset_index()
df_vars_modeling_dpto

indicador  anio  codigo_departamento  codigo_entidad  \
0          2016                    5            5000   
1          2016                    8            8000   
2          2016                   13           13000   
3          2016                   15           15000   
4          2016                   17           17000   
..          ...                  ...             ...   
91         2018                   91           91000   
92         2018                   94           94000   
93         2018                   95           95000   
94         2018                   97           97000   
95         2018                   99           99000   

indicador  promedio_del_componente_de_gestion_por_departamento_y_nacion  \
0                                                      53.58              
1                                                      43.68              
2                                                      38.87              
3                                                      49.53              
4                                                      50.53              
..                                                       ...              
91                                                     36.65              
92                                                     53.68              
93                                                     42.80              
94                                                     39.05              
95                                                     41.21              

indicador  promedio_del_componente_de_resultados_por_departamento_y_nacion  \
0                                                      69.22                 
1                                                      69.85                 
2                                                      64.78                 
3                                                      67.63                 
4                                                      70.06                 
..                                                       ...                 
91                                                     61.94                 
92                                                     61.60                 
93                                                     57.32                 
94                                                     65.46                 
95                                                     55.93                 

indicador  promedio_del_indicador_de_mdm_por_departamento_y_nacion  
0                                                      53.42        
1                                                      43.68        
2                                                      38.77        
3                                                      49.33        
4                                                      50.50        
..                                                       ...        
91                                                     36.45        
92                                                     52.27        
93                                                     43.17        
94                                                     39.98        
95                                                     41.63        

[96 rows x 6 columns]

# Economía

In [97]:
# We remove 'pib_-_base_2015' subcategory and its associate variables:
filtered_tabs_dpto_only[0] = filtered_tabs_dpto_only[0][filtered_tabs_dpto_only[0]['subcategoria']!='pib_-_base_2015']

In [98]:
df_vars_modeling_dpto = df_vars_modeling_dpto.merge(
    pd.pivot(filtered_tabs_dpto_only[0], index=['anio', 'codigo_departamento', 'codigo_entidad'], columns='indicador', values='dato_numerico').reset_index(),
    left_on=['codigo_entidad', 'codigo_departamento', 'anio'],
    right_on=['codigo_entidad', 'codigo_departamento','anio'],
    how='right'
)
df_vars_modeling_dpto

indicador  anio  codigo_departamento  codigo_entidad  \
0          2016                    5            5000   
1          2016                    8            8000   
2          2016                   13           13000   
3          2016                   15           15000   
4          2016                   17           17000   
..          ...                  ...             ...   
122        2019                   91           91000   
123        2019                   94           94000   
124        2019                   95           95000   
125        2019                   97           97000   
126        2019                   99           99000   

indicador  promedio_del_componente_de_gestion_por_departamento_y_nacion  \
0                                                      53.58              
1                                                      43.68              
2                                                      38.87              
3                                                      49.53              
4                                                      50.53              
..                                                       ...              
122                                                      NaN              
123                                                      NaN              
124                                                      NaN              
125                                                      NaN              
126                                                      NaN              

indicador  promedio_del_componente_de_resultados_por_departamento_y_nacion  \
0                                                      69.22                 
1                                                      69.85                 
2                                                      64.78                 
3                                                      67.63                 
4                                                      70.06                 
..                                                       ...                 
122                                                      NaN                 
123                                                      NaN                 
124                                                      NaN                 
125                                                      NaN                 
126                                                      NaN                 

indicador  promedio_del_indicador_de_mdm_por_departamento_y_nacion  \
0                                                      53.42         
1                                                      43.68         
2                                                      38.77         
3                                                      49.33         
4                                                      50.50         
..                                                       ...         
122                                                      NaN         
123                                                      NaN         
124                                                      NaN         
125                                                      NaN         
126                                                      NaN         

indicador  participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_actividades_artisticas;_de_entrenamiento_y_otros_servicios_(actividades_artisticas;_de_entretenimiento_y_recreacion_y_otras_actividades_de_servicios;_actividades_de_los_hogares_individuales_en_calidad_de_empleadores;_actividades_no_diferenciadas_de_los_hogares_individuales_como_productores_de_bienes_y_servicios_para_uso_propio)  \
0                                                      14.20                                                                                                                                     

# Justicia y Derecho

In [99]:
df_vars_modeling_dpto = df_vars_modeling_dpto.merge(
    pd.pivot(filtered_tabs_dpto_only[3], index=['anio', 'codigo_departamento', 'codigo_entidad'], columns='indicador', values='dato_numerico').reset_index(),
    left_on=['codigo_entidad', 'codigo_departamento', 'anio'],
    right_on=['codigo_entidad', 'codigo_departamento','anio'],
    how='right'
)
df_vars_modeling_dpto

indicador  anio  codigo_departamento  codigo_entidad  \
0          2016                    5            5000   
1          2016                    8            8000   
2          2016                   11           11001   
3          2016                   13           13000   
4          2016                   15           15000   
..          ...                  ...             ...   
127        2019                   91           91000   
128        2019                   94           94000   
129        2019                   95           95000   
130        2019                   97           97000   
131        2019                   99           99000   

indicador  promedio_del_componente_de_gestion_por_departamento_y_nacion  \
0                                                      53.58              
1                                                      43.68              
2                                                        NaN              
3                                                      38.87              
4                                                      49.53              
..                                                       ...              
127                                                      NaN              
128                                                      NaN              
129                                                      NaN              
130                                                      NaN              
131                                                      NaN              

indicador  promedio_del_componente_de_resultados_por_departamento_y_nacion  \
0                                                      69.22                 
1                                                      69.85                 
2                                                        NaN                 
3                                                      64.78                 
4                                                      67.63                 
..                                                       ...                 
127                                                      NaN                 
128                                                      NaN                 
129                                                      NaN                 
130                                                      NaN                 
131                                                      NaN                 

indicador  promedio_del_indicador_de_mdm_por_departamento_y_nacion  \
0                                                      53.42         
1                                                      43.68         
2                                                        NaN         
3                                                      38.77         
4                                                      49.33         
..                                                       ...         
127                                                      NaN         
128                                                      NaN         
129                                                      NaN         
130                                                      NaN         
131                                                      NaN         

indicador  participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_actividades_artisticas;_de_entrenamiento_y_otros_servicios_(actividades_artisticas;_de_entretenimiento_y_recreacion_y_otras_actividades_de_servicios;_actividades_de_los_hogares_individuales_en_calidad_de_empleadores;_actividades_no_diferenciadas_de_los_hogares_individuales_como_productores_de_bienes_y_servicios_para_uso_propio)  \
0                                                      14.20                                                                                                                                     

# Educación

In [100]:
df_vars_modeling_dpto = df_vars_modeling_dpto.merge(
    pd.pivot(filtered_tabs_dpto_only[4], index=['anio','codigo_entidad'], columns='indicador', values='dato_numerico').reset_index(),
    left_on=['codigo_entidad', 'anio'],
    right_on=['codigo_entidad','anio'],
    how='right'
)
df_vars_modeling_dpto

indicador  anio  codigo_departamento  codigo_entidad  \
0          2016                    5            5000   
1          2016                    8            8000   
2          2016                   11           11001   
3          2016                   13           13000   
4          2016                   15           15000   
..          ...                  ...             ...   
127        2019                   91           91000   
128        2019                   94           94000   
129        2019                   95           95000   
130        2019                   97           97000   
131        2019                   99           99000   

indicador  promedio_del_componente_de_gestion_por_departamento_y_nacion  \
0                                                      53.58              
1                                                      43.68              
2                                                        NaN              
3                                                      38.87              
4                                                      49.53              
..                                                       ...              
127                                                      NaN              
128                                                      NaN              
129                                                      NaN              
130                                                      NaN              
131                                                      NaN              

indicador  promedio_del_componente_de_resultados_por_departamento_y_nacion  \
0                                                      69.22                 
1                                                      69.85                 
2                                                        NaN                 
3                                                      64.78                 
4                                                      67.63                 
..                                                       ...                 
127                                                      NaN                 
128                                                      NaN                 
129                                                      NaN                 
130                                                      NaN                 
131                                                      NaN                 

indicador  promedio_del_indicador_de_mdm_por_departamento_y_nacion  \
0                                                      53.42         
1                                                      43.68         
2                                                        NaN         
3                                                      38.77         
4                                                      49.33         
..                                                       ...         
127                                                      NaN         
128                                                      NaN         
129                                                      NaN         
130                                                      NaN         
131                                                      NaN         

indicador  participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_actividades_artisticas;_de_entrenamiento_y_otros_servicios_(actividades_artisticas;_de_entretenimiento_y_recreacion_y_otras_actividades_de_servicios;_actividades_de_los_hogares_individuales_en_calidad_de_empleadores;_actividades_no_diferenciadas_de_los_hogares_individuales_como_productores_de_bienes_y_servicios_para_uso_propio)  \
0                                                      14.20                                                                                                                                     

# Vivienda y acceso a servicios públicos

In [101]:
df_vars_modeling_dpto = df_vars_modeling_dpto.merge(
    pd.pivot(filtered_tabs_dpto_only[8][filtered_tabs_dpto_only[8]['mes']==9], index=['anio', 'codigo_entidad'], columns='indicador', values='dato_numerico').reset_index(),
    left_on=['codigo_entidad', 'anio'],
    right_on=['codigo_entidad','anio'],
    how='left'
)
df_vars_modeling_dpto

indicador  anio  codigo_departamento  codigo_entidad  \
0          2016                    5            5000   
1          2016                    8            8000   
2          2016                   11           11001   
3          2016                   13           13000   
4          2016                   15           15000   
..          ...                  ...             ...   
127        2019                   91           91000   
128        2019                   94           94000   
129        2019                   95           95000   
130        2019                   97           97000   
131        2019                   99           99000   

indicador  promedio_del_componente_de_gestion_por_departamento_y_nacion  \
0                                                      53.58              
1                                                      43.68              
2                                                        NaN              
3                                                      38.87              
4                                                      49.53              
..                                                       ...              
127                                                      NaN              
128                                                      NaN              
129                                                      NaN              
130                                                      NaN              
131                                                      NaN              

indicador  promedio_del_componente_de_resultados_por_departamento_y_nacion  \
0                                                      69.22                 
1                                                      69.85                 
2                                                        NaN                 
3                                                      64.78                 
4                                                      67.63                 
..                                                       ...                 
127                                                      NaN                 
128                                                      NaN                 
129                                                      NaN                 
130                                                      NaN                 
131                                                      NaN                 

indicador  promedio_del_indicador_de_mdm_por_departamento_y_nacion  \
0                                                      53.42         
1                                                      43.68         
2                                                        NaN         
3                                                      38.77         
4                                                      49.33         
..                                                       ...         
127                                                      NaN         
128                                                      NaN         
129                                                      NaN         
130                                                      NaN         
131                                                      NaN         

indicador  participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_actividades_artisticas;_de_entrenamiento_y_otros_servicios_(actividades_artisticas;_de_entretenimiento_y_recreacion_y_otras_actividades_de_servicios;_actividades_de_los_hogares_individuales_en_calidad_de_empleadores;_actividades_no_diferenciadas_de_los_hogares_individuales_como_productores_de_bienes_y_servicios_para_uso_propio)  \
0                                                      14.20                                                                                                                                     

# Coflicto armado y seguridad ciudadana

In [102]:
df_vars_modeling_dpto = df_vars_modeling_dpto.merge(
    pd.pivot(filtered_tabs_dpto_only[9], index=['anio', 'codigo_entidad'], columns='indicador', values='dato_numerico').reset_index(),
    left_on=['codigo_entidad', 'anio'],
    right_on=['codigo_entidad','anio'],
    how='left'
)
df_vars_modeling_dpto

indicador  anio  codigo_departamento  codigo_entidad  \
0          2016                    5            5000   
1          2016                    8            8000   
2          2016                   11           11001   
3          2016                   13           13000   
4          2016                   15           15000   
..          ...                  ...             ...   
127        2019                   91           91000   
128        2019                   94           94000   
129        2019                   95           95000   
130        2019                   97           97000   
131        2019                   99           99000   

indicador  promedio_del_componente_de_gestion_por_departamento_y_nacion  \
0                                                      53.58              
1                                                      43.68              
2                                                        NaN              
3                                                      38.87              
4                                                      49.53              
..                                                       ...              
127                                                      NaN              
128                                                      NaN              
129                                                      NaN              
130                                                      NaN              
131                                                      NaN              

indicador  promedio_del_componente_de_resultados_por_departamento_y_nacion  \
0                                                      69.22                 
1                                                      69.85                 
2                                                        NaN                 
3                                                      64.78                 
4                                                      67.63                 
..                                                       ...                 
127                                                      NaN                 
128                                                      NaN                 
129                                                      NaN                 
130                                                      NaN                 
131                                                      NaN                 

indicador  promedio_del_indicador_de_mdm_por_departamento_y_nacion  \
0                                                      53.42         
1                                                      43.68         
2                                                        NaN         
3                                                      38.77         
4                                                      49.33         
..                                                       ...         
127                                                      NaN         
128                                                      NaN         
129                                                      NaN         
130                                                      NaN         
131                                                      NaN         

indicador  participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_actividades_artisticas;_de_entrenamiento_y_otros_servicios_(actividades_artisticas;_de_entretenimiento_y_recreacion_y_otras_actividades_de_servicios;_actividades_de_los_hogares_individuales_en_calidad_de_empleadores;_actividades_no_diferenciadas_de_los_hogares_individuales_como_productores_de_bienes_y_servicios_para_uso_propio)  \
0                                                      14.20                                                                                                                                     

# Salud

In [103]:
df_vars_modeling_dpto = df_vars_modeling_dpto.merge(
    pd.pivot(filtered_tabs_dpto_only[10], index=['anio', 'codigo_entidad'], columns='indicador', values='dato_numerico').reset_index(),
    left_on=['codigo_entidad', 'anio'],
    right_on=['codigo_entidad','anio'],
    how='right'
)
df_vars_modeling_dpto

indicador  anio  codigo_departamento  codigo_entidad  \
0          2016                    5            5000   
1          2016                    8            8000   
2          2016                   11           11001   
3          2016                   13           13000   
4          2016                   15           15000   
..          ...                  ...             ...   
127        2019                   91           91000   
128        2019                   94           94000   
129        2019                   95           95000   
130        2019                   97           97000   
131        2019                   99           99000   

indicador  promedio_del_componente_de_gestion_por_departamento_y_nacion  \
0                                                      53.58              
1                                                      43.68              
2                                                        NaN              
3                                                      38.87              
4                                                      49.53              
..                                                       ...              
127                                                      NaN              
128                                                      NaN              
129                                                      NaN              
130                                                      NaN              
131                                                      NaN              

indicador  promedio_del_componente_de_resultados_por_departamento_y_nacion  \
0                                                      69.22                 
1                                                      69.85                 
2                                                        NaN                 
3                                                      64.78                 
4                                                      67.63                 
..                                                       ...                 
127                                                      NaN                 
128                                                      NaN                 
129                                                      NaN                 
130                                                      NaN                 
131                                                      NaN                 

indicador  promedio_del_indicador_de_mdm_por_departamento_y_nacion  \
0                                                      53.42         
1                                                      43.68         
2                                                        NaN         
3                                                      38.77         
4                                                      49.33         
..                                                       ...         
127                                                      NaN         
128                                                      NaN         
129                                                      NaN         
130                                                      NaN         
131                                                      NaN         

indicador  participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_actividades_artisticas;_de_entrenamiento_y_otros_servicios_(actividades_artisticas;_de_entretenimiento_y_recreacion_y_otras_actividades_de_servicios;_actividades_de_los_hogares_individuales_en_calidad_de_empleadores;_actividades_no_diferenciadas_de_los_hogares_individuales_como_productores_de_bienes_y_servicios_para_uso_propio)  \
0                                                      14.20                                                                                                                                     

# Finanzas públicas

In [104]:
filtered_tabs_dpto_only[11]['mes'].unique()

array([12,  3,  6,  9])

In [105]:
anual_vars_finances_dpto, more_than_anual_vars_finances_dpto = detect_more_than_yearly_vars(filtered_tabs_dpto_only[11])

print('Quantity of variables measured annually: ',len(anual_vars_finances_dpto),'\nQuantity of variables measured more than once in a year: ', len(more_than_anual_vars_finances_dpto))

Quantity of variables measured annually:  45 
Quantity of variables measured more than once in a year:  5


In [106]:
filtered_tabs_dpto_only[11] = filtered_tabs_dpto_only[11][filtered_tabs_dpto_only[11]['indicador'].isin(anual_vars_finances_dpto)]
filtered_tabs_dpto_only[11].head()

codigo_departamento              departamento codigo_entidad  \
18226                  44                la_guajira          44000   
18322                  68                 santander          68000   
18370                   5                 antioquia           5000   
18395                  15                    boyaca          15000   
18408                  88  san_andres_y_providencia          88000   

                        entidad          dimension  \
18226                la_guajira  finanzas_publicas   
18322                 santander  finanzas_publicas   
18370                 antioquia  finanzas_publicas   
18395                    boyaca  finanzas_publicas   
18408  san_andres_y_providencia  finanzas_publicas   

                        subcategoria         indicador  dato_numerico  \
18226  operaciones_efectivas_de_caja  ingresos_totales       81043.11   
18322  operaciones_efectivas_de_caja  ingresos_totales       30771.69   
18370  operaciones_efectivas_de_caja  ingresos_totales       71813.63   
18395  operaciones_efectivas_de_caja  ingresos_totales       13896.47   
18408  operaciones_efectivas_de_caja  ingresos_totales       51565.43   

       dato_cualitativo  anio  mes                               fuente  \
18226               NaN  2016   12  dnp_a_partir_de_informacion_del_fut   
18322               NaN  2016   12  dnp_a_partir_de_informacion_del_fut   
18370               NaN  2016   12  dnp_a_partir_de_informacion_del_fut   
18395               NaN  2016   12  dnp_a_partir_de_informacion_del_fut   
18408               NaN  2016   12  dnp_a_partir_de_informacion_del_fut   

                   unidad_de_medida  
18226  millones_de_pesos_corrientes  
18322  millones_de_pesos_corrientes  
18370  millones_de_pesos_corrientes  
18395  millones_de_pesos_corrientes  
18408  millones_de_pesos_corrientes

In [107]:
filtered_tabs_dpto_only[11]['subcategoria'].unique()

array(['operaciones_efectivas_de_caja', 'resumen_recursos',
       'sgp_-_distribucion_asignaciones_sgp_por_sectores',
       'sgp_-_porcentaje_de_ejecucion_presupuestal_por_sector',
       'recursos_propios', 'desempenio_fiscal',
       'sgp_-_distribucion_porcentual_de_asignaciones_sgp_por_sectores'],
      dtype=object)

In [108]:
df_vars_modeling_dpto = df_vars_modeling_dpto.merge(
    pd.pivot(filtered_tabs_dpto_only[11][filtered_tabs_dpto_only[11]['subcategoria'].isin(['operaciones_efectivas_de_caja', 'resumen_recursos', 'desempenio_fiscal','sgp_-_distribucion_porcentual_de_asignaciones_sgp_por_sectores'])],index=['anio','codigo_entidad'], columns='indicador',values='dato_numerico'),
    left_on=['codigo_entidad', 'anio'],
    right_on=['codigo_entidad','anio'],
    how='right'
)
df_vars_modeling_dpto

indicador  anio  codigo_departamento  codigo_entidad  \
0          2016                    5            5000   
1          2016                    8            8000   
2          2016                   11           11001   
3          2016                   13           13000   
4          2016                   15           15000   
..          ...                  ...             ...   
127        2019                   91           91000   
128        2019                   94           94000   
129        2019                   95           95000   
130        2019                   97           97000   
131        2019                   99           99000   

indicador  promedio_del_componente_de_gestion_por_departamento_y_nacion  \
0                                                      53.58              
1                                                      43.68              
2                                                        NaN              
3                                                      38.87              
4                                                      49.53              
..                                                       ...              
127                                                      NaN              
128                                                      NaN              
129                                                      NaN              
130                                                      NaN              
131                                                      NaN              

indicador  promedio_del_componente_de_resultados_por_departamento_y_nacion  \
0                                                      69.22                 
1                                                      69.85                 
2                                                        NaN                 
3                                                      64.78                 
4                                                      67.63                 
..                                                       ...                 
127                                                      NaN                 
128                                                      NaN                 
129                                                      NaN                 
130                                                      NaN                 
131                                                      NaN                 

indicador  promedio_del_indicador_de_mdm_por_departamento_y_nacion  \
0                                                      53.42         
1                                                      43.68         
2                                                        NaN         
3                                                      38.77         
4                                                      49.33         
..                                                       ...         
127                                                      NaN         
128                                                      NaN         
129                                                      NaN         
130                                                      NaN         
131                                                      NaN         

indicador  participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_actividades_artisticas;_de_entrenamiento_y_otros_servicios_(actividades_artisticas;_de_entretenimiento_y_recreacion_y_otras_actividades_de_servicios;_actividades_de_los_hogares_individuales_en_calidad_de_empleadores;_actividades_no_diferenciadas_de_los_hogares_individuales_como_productores_de_bienes_y_servicios_para_uso_propio)  \
0                                                      14.20                                                                                                                                     

# Censo 2005 y proyecciones DANE

In [109]:
df_vars_modeling_dpto = df_vars_modeling_dpto.merge(
    pd.pivot(filtered_tabs_dpto_only[12], index=['anio', 'codigo_entidad'], columns='indicador', values='dato_numerico').reset_index(),
    left_on=['codigo_entidad', 'anio'],
    right_on=['codigo_entidad','anio'],
    how='right'
)
df_vars_modeling_dpto

indicador  anio  codigo_departamento  codigo_entidad  \
0          2016                    5            5000   
1          2016                    8            8000   
2          2016                   11           11001   
3          2016                   13           13000   
4          2016                   15           15000   
..          ...                  ...             ...   
127        2019                   91           91000   
128        2019                   94           94000   
129        2019                   95           95000   
130        2019                   97           97000   
131        2019                   99           99000   

indicador  promedio_del_componente_de_gestion_por_departamento_y_nacion  \
0                                                      53.58              
1                                                      43.68              
2                                                        NaN              
3                                                      38.87              
4                                                      49.53              
..                                                       ...              
127                                                      NaN              
128                                                      NaN              
129                                                      NaN              
130                                                      NaN              
131                                                      NaN              

indicador  promedio_del_componente_de_resultados_por_departamento_y_nacion  \
0                                                      69.22                 
1                                                      69.85                 
2                                                        NaN                 
3                                                      64.78                 
4                                                      67.63                 
..                                                       ...                 
127                                                      NaN                 
128                                                      NaN                 
129                                                      NaN                 
130                                                      NaN                 
131                                                      NaN                 

indicador  promedio_del_indicador_de_mdm_por_departamento_y_nacion  \
0                                                      53.42         
1                                                      43.68         
2                                                        NaN         
3                                                      38.77         
4                                                      49.33         
..                                                       ...         
127                                                      NaN         
128                                                      NaN         
129                                                      NaN         
130                                                      NaN         
131                                                      NaN         

indicador  participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_actividades_artisticas;_de_entrenamiento_y_otros_servicios_(actividades_artisticas;_de_entretenimiento_y_recreacion_y_otras_actividades_de_servicios;_actividades_de_los_hogares_individuales_en_calidad_de_empleadores;_actividades_no_diferenciadas_de_los_hogares_individuales_como_productores_de_bienes_y_servicios_para_uso_propio)  \
0                                                      14.20                                                                                                                                     

# Seguridad marítima y fluvial

# Pobreza

In [110]:
df_vars_modeling_dpto = df_vars_modeling_dpto.merge(
    pd.pivot(filtered_tabs_dpto_only[16], index=['anio', 'codigo_entidad'], columns='indicador', values='dato_numerico').reset_index(),
    left_on=['codigo_entidad', 'anio'],
    right_on=['codigo_entidad','anio'],
    how='left'
)
df_vars_modeling_dpto

indicador  anio  codigo_departamento  codigo_entidad  \
0          2016                    5            5000   
1          2016                    8            8000   
2          2016                   11           11001   
3          2016                   13           13000   
4          2016                   15           15000   
..          ...                  ...             ...   
127        2019                   91           91000   
128        2019                   94           94000   
129        2019                   95           95000   
130        2019                   97           97000   
131        2019                   99           99000   

indicador  promedio_del_componente_de_gestion_por_departamento_y_nacion  \
0                                                      53.58              
1                                                      43.68              
2                                                        NaN              
3                                                      38.87              
4                                                      49.53              
..                                                       ...              
127                                                      NaN              
128                                                      NaN              
129                                                      NaN              
130                                                      NaN              
131                                                      NaN              

indicador  promedio_del_componente_de_resultados_por_departamento_y_nacion  \
0                                                      69.22                 
1                                                      69.85                 
2                                                        NaN                 
3                                                      64.78                 
4                                                      67.63                 
..                                                       ...                 
127                                                      NaN                 
128                                                      NaN                 
129                                                      NaN                 
130                                                      NaN                 
131                                                      NaN                 

indicador  promedio_del_indicador_de_mdm_por_departamento_y_nacion  \
0                                                      53.42         
1                                                      43.68         
2                                                        NaN         
3                                                      38.77         
4                                                      49.33         
..                                                       ...         
127                                                      NaN         
128                                                      NaN         
129                                                      NaN         
130                                                      NaN         
131                                                      NaN         

indicador  participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_actividades_artisticas;_de_entrenamiento_y_otros_servicios_(actividades_artisticas;_de_entretenimiento_y_recreacion_y_otras_actividades_de_servicios;_actividades_de_los_hogares_individuales_en_calidad_de_empleadores;_actividades_no_diferenciadas_de_los_hogares_individuales_como_productores_de_bienes_y_servicios_para_uso_propio)  \
0                                                      14.20                                                                                                                                     

# Selecting features:

In [111]:
# First we select only features with complete data for at least 2016-2018:
df_vars_modeling_dpto = df_vars_modeling_dpto.drop(columns=list(df_vars_modeling_dpto.describe().transpose()[df_vars_modeling_dpto.describe().transpose()['count']<96].transpose().columns))
df_vars_modeling_dpto

indicador  anio  codigo_departamento  codigo_entidad  \
0          2016                    5            5000   
1          2016                    8            8000   
2          2016                   11           11001   
3          2016                   13           13000   
4          2016                   15           15000   
..          ...                  ...             ...   
127        2019                   91           91000   
128        2019                   94           94000   
129        2019                   95           95000   
130        2019                   97           97000   
131        2019                   99           99000   

indicador  promedio_del_componente_de_gestion_por_departamento_y_nacion  \
0                                                      53.58              
1                                                      43.68              
2                                                        NaN              
3                                                      38.87              
4                                                      49.53              
..                                                       ...              
127                                                      NaN              
128                                                      NaN              
129                                                      NaN              
130                                                      NaN              
131                                                      NaN              

indicador  promedio_del_componente_de_resultados_por_departamento_y_nacion  \
0                                                      69.22                 
1                                                      69.85                 
2                                                        NaN                 
3                                                      64.78                 
4                                                      67.63                 
..                                                       ...                 
127                                                      NaN                 
128                                                      NaN                 
129                                                      NaN                 
130                                                      NaN                 
131                                                      NaN                 

indicador  promedio_del_indicador_de_mdm_por_departamento_y_nacion  \
0                                                      53.42         
1                                                      43.68         
2                                                        NaN         
3                                                      38.77         
4                                                      49.33         
..                                                       ...         
127                                                      NaN         
128                                                      NaN         
129                                                      NaN         
130                                                      NaN         
131                                                      NaN         

indicador  participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_actividades_artisticas;_de_entrenamiento_y_otros_servicios_(actividades_artisticas;_de_entretenimiento_y_recreacion_y_otras_actividades_de_servicios;_actividades_de_los_hogares_individuales_en_calidad_de_empleadores;_actividades_no_diferenciadas_de_los_hogares_individuales_como_productores_de_bienes_y_servicios_para_uso_propio)  \
0                                                      14.20                                                                                                                                     

In [112]:
corr = df_vars_modeling_dpto.corr()

In [113]:
# fig, ax = plt.subplots(figsize=(15, 15))
# sns.heatmap(corr, annot = True, cmap = 'coolwarm', vmin = -1, vmax = 1)

In [114]:
corr

indicador                                                   anio  \
indicador                                                          
anio                                                1.000000e+00   
codigo_departamento                                 7.242860e-15   
codigo_entidad                                      7.163711e-15   
promedio_del_componente_de_gestion_por_departam...  1.690474e-01   
promedio_del_componente_de_resultados_por_depar...  5.434589e-02   
...                                                          ...   
proyeccion_de_poblacion_entre_los_5_y_9_anios       2.281195e-03   
proyeccion_de_poblacion_entre_los_60_y_64_anios     3.406820e-02   
proyeccion_de_poblacion_entre_los_65_y_69_anios     3.441696e-02   
proyeccion_de_poblacion_entre_los_70_y_74_anios     4.007774e-02   
proyeccion_de_poblacion_entre_los_75_y_79_anios     1.613118e-02   

indicador                                           codigo_departamento  \
indicador                                                                 
anio                                                       7.242860e-15   
codigo_departamento                                        1.000000e+00   
codigo_entidad                                             1.000000e+00   
promedio_del_componente_de_gestion_por_departam...        -1.659984e-01   
promedio_del_componente_de_resultados_por_depar...        -4.469872e-01   
...                                                                 ...   
proyeccion_de_poblacion_entre_los_5_y_9_anios             -5.607235e-01   
proyeccion_de_poblacion_entre_los_60_y_64_anios           -4.746598e-01   
proyeccion_de_poblacion_entre_los_65_y_69_anios           -4.754853e-01   
proyeccion_de_poblacion_entre_los_70_y_74_anios           -4.759747e-01   
proyeccion_de_poblacion_entre_los_75_y_79_anios           -4.797003e-01   

indicador                                           codigo_entidad  \
indicador                                                            
anio                                                  7.163711e-15   
codigo_departamento                                   1.000000e+00   
codigo_entidad                                        1.000000e+00   
promedio_del_componente_de_gestion_por_departam...   -1.659984e-01   
promedio_del_componente_de_resultados_por_depar...   -4.469872e-01   
...                                                            ...   
proyeccion_de_poblacion_entre_los_5_y_9_anios        -5.607208e-01   
proyeccion_de_poblacion_entre_los_60_y_64_anios      -4.746567e-01   
proyeccion_de_poblacion_entre_los_65_y_69_anios      -4.754822e-01   
proyeccion_de_poblacion_entre_los_70_y_74_anios      -4.759716e-01   
proyeccion_de_poblacion_entre_los_75_y_79_anios      -4.796974e-01   

indicador                                           promedio_del_componente_de_gestion_por_departamento_y_nacion  \
indicador                                                                                                          
anio                                                                                         0.169047              
codigo_departamento                                                                         -0.165998              
codigo_entidad                                                                              -0.165998              
promedio_del_componente_de_gestion_por_departam...                                           1.000000              
promedio_del_componente_de_resultados_por_depar...                                           0.432195              
...                                                                                               ...              
proyeccion_de_poblacion_entre_los_5_y_9_anios                                                0.362533              
proyeccion_de_poblacion_entre_los_60_y_64_anios                                              0.442780              
proyeccion_de_poblacion_entre_los_65_y_69_anios                     

In [115]:
cols_high_corr = []
rows_high_corr = []
values_high_corr = []
for col in corr.columns:
    for key, value in corr[col].iteritems():
        if ((value > 0.9) & (value < 1.0)) | ((value < -0.9) & (value > -1.0)):
            cols_high_corr.append(col)
            rows_high_corr.append(key)
            values_high_corr.append(value)

correlated_vars = pd.DataFrame({'var_1':cols_high_corr, 'var_2':rows_high_corr, 'corr_coeff':values_high_corr}).drop_duplicates('corr_coeff')

In [116]:
print(len(correlated_vars['var_1'].unique()))
print(len(correlated_vars))
correlated_vars.head()

170
4224


var_1  \
0                                codigo_departamento   
2  promedio_del_componente_de_gestion_por_departa...   
4  participacion_de_las_actividades_economicas_de...   
5  participacion_de_las_actividades_economicas_de...   
6  participacion_de_las_actividades_economicas_de...   

                                               var_2  corr_coeff  
0                                     codigo_entidad    1.000000  
2  promedio_del_indicador_de_mdm_por_departamento...    0.998136  
4  participacion_de_las_actividades_economicas_de...    0.988204  
5  participacion_de_las_actividades_economicas_de...    0.964999  
6  participacion_de_las_actividades_economicas_de...    0.982471

In [117]:
unique_corr_vars = pd.DataFrame({'var_1_unique': correlated_vars['var_1'].unique(), 'var_2_unique':correlated_vars['var_2'].unique()})

In [118]:
#unique_corr_vars.to_csv('../../data/highly_correlated_vars_by_department.csv', index=False)

In [119]:
vars_to_drop = []
for i in range(len(unique_corr_vars)):
    for j in range(len(unique_corr_vars)):
        if unique_corr_vars['var_1_unique'].iloc[i] == unique_corr_vars['var_2_unique'].iloc[j]:
            vars_to_drop.append(unique_corr_vars['var_1_unique'].iloc[i])
len(vars_to_drop)

148

In [120]:
set(unique_corr_vars['var_1_unique'])-set(vars_to_drop)

{'cobertura_bruta_en_educacion_-_total',
 'cobertura_bruta_en_educacion_media',
 'codigo_departamento',
 'deficit_o_ahorro_corriente',
 'deficit_o_superavit_total',
 'gastos_corrientes_per_capita',
 'participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_actividades_artisticas;_de_entrenamiento_y_otros_servicios_(actividades_artisticas;_de_entretenimiento_y_recreacion_y_otras_actividades_de_servicios;_actividades_de_los_hogares_individuales_en_calidad_de_empleadores;_actividades_no_diferenciadas_de_los_hogares_individuales_como_productores_de_bienes_y_servicios_para_uso_propio)',
 'participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_agricultura;_ganaderia;_caza;_silvicultura_y_pesca_(agricultura;_ganaderia;_caza;_silvicultura_y_pesca)',
 'participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_explotacion_de_minas_y_ca

In [121]:
df_vars_modeling_dpto = df_vars_modeling_dpto.drop(columns=vars_to_drop)

In [122]:
corr2 = df_vars_modeling_dpto.corr()

In [123]:
cols_high_corr = []
rows_high_corr = []
values_high_corr = []
for col in corr2.columns:
    for key, value in corr2[col].iteritems():
        if ((value > 0.9) & (value < 1.0)) | ((value < -0.9) & (value > -1.0)):
            cols_high_corr.append(col)
            rows_high_corr.append(key)
            values_high_corr.append(value)

correlated_vars2 = pd.DataFrame({'var_1':cols_high_corr, 'var_2':rows_high_corr, 'corr_coeff':values_high_corr}).drop_duplicates('corr_coeff')

In [124]:
correlated_vars2

var_1  \
0                                 codigo_departamento   
2   promedio_del_componente_de_gestion_por_departa...   
4   participacion_de_las_actividades_economicas_de...   
5   participacion_de_las_actividades_economicas_de...   
6   participacion_de_las_actividades_economicas_de...   
7                                      pib_per_capita   
11               cobertura_bruta_en_educacion_-_total   
12                 cobertura_bruta_en_educacion_media   
15  puntaje_promedio_pruebas_saber_11_-_lectura_cr...   
17  porcentaje_de_nacidos_vivos_con_4_o_mas_consul...   
19                         deficit_o_ahorro_corriente   
20                          deficit_o_superavit_total   
22                       gastos_corrientes_per_capita   
23                       gastos_corrientes_per_capita   
27  porcentaje_de_poblacion_de_80_o_mas_anios;_del...   
28       porcentaje_de_poblacion_de_hombres_de__20-24   
29       porcentaje_de_poblacion_de_hombres_de__25-29   
30       porcentaje_de_poblacion_de_hombres_de__30-34   
31       porcentaje_de_poblacion_de_hombres_de__35-39   
32       porcentaje_de_poblacion_de_mujeres_de__25-29   
39                    porcentaje_poblacion_de_hombres   

                                                var_2  corr_coeff  
0                                      codigo_entidad    1.000000  
2   promedio_del_indicador_de_mdm_por_departamento...    0.998136  
4     proyeccion_de_poblacion_entre_los_75_y_79_anios    0.957675  
5   pib_por_actividades_economicas_-_agricultura;_...    0.999128  
6   pib_por_actividades_economicas_-_explotacion_d...    0.990525  
7   pib_per_capita_como_porcentaje_del_promedio_na...    0.994386  
11               cobertura_neta_en_educacion_primaria    0.951661  
12             cobertura_neta_en_educacion_secundaria    0.947733  
15    puntaje_promedio_pruebas_saber_11_-_matematicas    0.934678  
17                   promedio_de_controles_prenatales    0.956948  
19                               densidad_poblacional    0.921981  
20                                     financiamiento   -0.908912  
22                          gastos_totales_per_capita    0.918847  
23  transferencias_per_capita_de_los_ingresos_corr...    0.927911  
27  porcentaje_de_poblacion_entre_los_75_y_79_anio...    0.967847  
28  porcentaje_de_poblacion_entre_los_20_y_24_anio...    0.988318  
29  porcentaje_de_poblacion_entre_los_25_y_29_anio...    0.965174  
30  porcentaje_de_poblacion_entre_los_30_y_34_anio...    0.977852  
31  porcentaje_de_poblacion_entre_los_40_y_44_anio...    0.936201  
32  porcentaje_de_poblacion_entre_los_25_y_29_anio...    0.978103  
39                    porcentaje_poblacion_de_mujeres   -0.999999

In [125]:
unique_corr_vars2 = pd.DataFrame({'var_1_unique': correlated_vars2['var_1'].unique(), 'var_2_unique':correlated_vars2['var_2'].unique()})
unique_corr_vars2

var_1_unique  \
0                                 codigo_departamento   
1   promedio_del_componente_de_gestion_por_departa...   
2   participacion_de_las_actividades_economicas_de...   
3   participacion_de_las_actividades_economicas_de...   
4   participacion_de_las_actividades_economicas_de...   
5                                      pib_per_capita   
6                cobertura_bruta_en_educacion_-_total   
7                  cobertura_bruta_en_educacion_media   
8   puntaje_promedio_pruebas_saber_11_-_lectura_cr...   
9   porcentaje_de_nacidos_vivos_con_4_o_mas_consul...   
10                         deficit_o_ahorro_corriente   
11                          deficit_o_superavit_total   
12                       gastos_corrientes_per_capita   
13  porcentaje_de_poblacion_de_80_o_mas_anios;_del...   
14       porcentaje_de_poblacion_de_hombres_de__20-24   
15       porcentaje_de_poblacion_de_hombres_de__25-29   
16       porcentaje_de_poblacion_de_hombres_de__30-34   
17       porcentaje_de_poblacion_de_hombres_de__35-39   
18       porcentaje_de_poblacion_de_mujeres_de__25-29   
19                    porcentaje_poblacion_de_hombres   

                                         var_2_unique  
0                                      codigo_entidad  
1   promedio_del_indicador_de_mdm_por_departamento...  
2     proyeccion_de_poblacion_entre_los_75_y_79_anios  
3   pib_por_actividades_economicas_-_agricultura;_...  
4   pib_por_actividades_economicas_-_explotacion_d...  
5   pib_per_capita_como_porcentaje_del_promedio_na...  
6                cobertura_neta_en_educacion_primaria  
7              cobertura_neta_en_educacion_secundaria  
8     puntaje_promedio_pruebas_saber_11_-_matematicas  
9                    promedio_de_controles_prenatales  
10                               densidad_poblacional  
11                                     financiamiento  
12                          gastos_totales_per_capita  
13  transferencias_per_capita_de_los_ingresos_corr...  
14  porcentaje_de_poblacion_entre_los_75_y_79_anio...  
15  porcentaje_de_poblacion_entre_los_20_y_24_anio...  
16  porcentaje_de_poblacion_entre_los_25_y_29_anio...  
17  porcentaje_de_poblacion_entre_los_30_y_34_anio...  
18  porcentaje_de_poblacion_entre_los_40_y_44_anio...  
19                    porcentaje_poblacion_de_mujeres

In [126]:
print(unique_corr_vars2['var_1_unique'].iloc[1], unique_corr_vars2['var_1_unique'].iloc[2], unique_corr_vars2['var_1_unique'].iloc[3])

promedio_del_componente_de_gestion_por_departamento_y_nacion participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_actividades_artisticas;_de_entrenamiento_y_otros_servicios_(actividades_artisticas;_de_entretenimiento_y_recreacion_y_otras_actividades_de_servicios;_actividades_de_los_hogares_individuales_en_calidad_de_empleadores;_actividades_no_diferenciadas_de_los_hogares_individuales_como_productores_de_bienes_y_servicios_para_uso_propio) participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_agricultura;_ganaderia;_caza;_silvicultura_y_pesca_(agricultura;_ganaderia;_caza;_silvicultura_y_pesca)


In [127]:
vars_to_drop2 = [
    'promedio_del_indicador_de_mdm_por_departamento_y_nacion', 'proyeccion_de_poblacion_entre_los_75_y_79_anios', 'cobertura_neta_en_educacion_primaria', 
    'cobertura_neta_en_educacion_secundaria', 'puntaje_promedio_pruebas_saber_11_-_matematicas', 'deficit_o_ahorro_corriente', 'porcentaje_de_poblacion_de_80_o_mas_anios;_del_total_de_poblacion_proyectada_para_la_entidad_territorial',
    'porcentaje_de_poblacion_entre_los_20_y_24_anios;_del_total_de_poblacion_proyectada_para_la_entidad_territorial','porcentaje_de_poblacion_entre_los_25_y_29_anios;_del_total_de_poblacion_proyectada_para_la_entidad_territorial',
    'porcentaje_de_poblacion_entre_los_30_y_34_anios;_del_total_de_poblacion_proyectada_para_la_entidad_territorial', 'porcentaje_de_poblacion_entre_los_40_y_44_anios;_del_total_de_poblacion_proyectada_para_la_entidad_territorial',
    'porcentaje_de_poblacion_entre_los_75_y_79_anios;_del_total_de_poblacion_proyectada_para_la_entidad_territorial', 'porcentaje_poblacion_de_hombres'
]

In [128]:
df_vars_modeling_dpto = df_vars_modeling_dpto.drop(columns=vars_to_drop2)

In [129]:
corr3 = df_vars_modeling_dpto.corr()

In [130]:
cols_high_corr = []
rows_high_corr = []
values_high_corr = []
for col in corr3.columns:
    for key, value in corr3[col].iteritems():
        if ((value > 0.9) & (value < 1.0)) | ((value < -0.9) & (value > -1.0)):
            cols_high_corr.append(col)
            rows_high_corr.append(key)
            values_high_corr.append(value)

correlated_vars3 = pd.DataFrame({'var_1':cols_high_corr, 'var_2':rows_high_corr, 'corr_coeff':values_high_corr}).drop_duplicates('corr_coeff')

In [131]:
correlated_vars3

var_1  \
0                                 codigo_departamento   
2   participacion_de_las_actividades_economicas_de...   
3   participacion_de_las_actividades_economicas_de...   
4                                      pib_per_capita   
8   porcentaje_de_nacidos_vivos_con_4_o_mas_consul...   
10                          deficit_o_superavit_total   
12                       gastos_corrientes_per_capita   
13                       gastos_corrientes_per_capita   

                                                var_2  corr_coeff  
0                                      codigo_entidad    1.000000  
2   pib_por_actividades_economicas_-_agricultura;_...    0.999128  
3   pib_por_actividades_economicas_-_explotacion_d...    0.990525  
4   pib_per_capita_como_porcentaje_del_promedio_na...    0.994386  
8                    promedio_de_controles_prenatales    0.956948  
10                                     financiamiento   -0.908912  
12                          gastos_totales_per_capita    0.918847  
13  transferencias_per_capita_de_los_ingresos_corr...    0.927911

In [132]:
print(list(correlated_vars3['var_1']))

['codigo_departamento', 'participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_agricultura;_ganaderia;_caza;_silvicultura_y_pesca_(agricultura;_ganaderia;_caza;_silvicultura_y_pesca)', 'participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_explotacion_de_minas_y_canteras_(explotacion_de_minas_y_canteras)', 'pib_per_capita', 'porcentaje_de_nacidos_vivos_con_4_o_mas_consultas_de_control_prenatal', 'deficit_o_superavit_total', 'gastos_corrientes_per_capita', 'gastos_corrientes_per_capita']


In [133]:
vars_to_drop3 = ['participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_agricultura;_ganaderia;_caza;_silvicultura_y_pesca_(agricultura;_ganaderia;_caza;_silvicultura_y_pesca)', 'participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_explotacion_de_minas_y_canteras_(explotacion_de_minas_y_canteras)', 
'participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_explotacion_de_minas_y_canteras_(explotacion_de_minas_y_canteras)',
'promedio_de_controles_prenatales', 'financiamiento', 'gastos_corrientes_per_capita']

In [134]:
df_vars_modeling_dpto = df_vars_modeling_dpto.drop(columns=vars_to_drop3)

In [135]:
df_investments_dpto = pd.read_csv('/Users/SebastianGuzman/Documents/DS4A-Final_Project/data/var_dep_filtered-2.csv', index_col=False)

In [136]:
df_investments_dpto.head()

anio_corte  departame_cod departame_nombre  cobertura_media_neta  \
0        2016             11           bogota              0.497000   
1        2016             13          bolivar              0.334391   
2        2016             15           boyaca              0.490642   
3        2016             17           caldas              0.412630   
4        2016             18          caqueta              0.214812   

   saber_11_matematicas  saber_11_lenguaje  cobertura_transicion  \
0             54.090000          54.350000              0.564000   
1             42.556739          45.795652              0.510957   
2             52.212520          51.290244              0.569244   
3             47.271852          49.739259              0.472778   
4             43.844375          45.901250              0.387750   

   cobertura_salud  vacunacion_pentavalente  mortalidad_infantil  \
0         0.924000                 0.956000            11.730000   
1         0.822130                 0.790543            22.100652   
2         0.773033                 0.886130            17.035691   
3         0.827259                 0.923815            14.015926   
4         0.720562                 0.727563            21.023125   

   cobertura_electrica_rural  cobertura_internet  cobertura_acueducto  \
0                   1.000000            0.211000             0.960000   
1                   0.765652            0.270870             0.568043   
2                   0.922541            0.163683             0.533415   
3                   0.991111            0.044481             0.694444   
4                   0.562500            0.162750             0.556875   

   cobertura_alcantarillado        hurtos  hurtos_x_10000_hab   homicidios  \
0                  0.960000  34364.000000           43.060000  1278.000000   
1                  0.217609     44.000000            2.797609     8.934783   
2                  0.265203     26.821138           11.426911     0.869919   
3                  0.454074     93.962963            9.064444     7.962963   
4                  0.531250     97.187500           13.487500     8.875000   

   homicidios_x_10000_hab  violencia_intrafamiliar  \
0                1.600000              4738.000000   
1                1.270217                18.239130   
2                0.935528                25.642276   
3                2.106296                27.777778   
4                2.468125                31.625000   

   violencia_intrafamiliar_x_10000_hab        mdm  conectividad  \
0                             5.940000  77.560000  3.916084e+09   
1                             2.694348  38.773043  3.540095e+10   
2                            13.514228  49.328537  3.204076e+10   
3                             5.685926  50.502963  1.629884e+10   
4                             5.510625  44.633750  1.883932e+10   

   transformacion  inversion_total  vacunacion_pentavalente_0_1_mean  \
0    2.094678e+10     2.486286e+10                          0.956000   
1    1.586348e+10     5.126443e+10                          0.790543   
2    1.176500e+10     4.380576e+10                          0.886130   
3    1.082415e+10     2.712298e+10                          0.923815   
4    4.330740e+09     2.317006e+10                          0.727563   

   componente_de_resultados_mean  componente_de_gestion_mean  \
0                       0.761400                    0.763900   
1                       0.647800                    0.388726   
2                       0.676331                    0.495280   
3                       0.700570                    0.505281   
4                       0.598856                    0.447319   

   gobierno_abierto_y_transparencia_mean  ejecucion_de_recursos_mean  \
0                               0.979100                    0.748700   
1                               0.576387                    0.662178   
2                               0.782495                    0.621669   
3               

In [137]:
df_vars_modeling_dpto

indicador  anio  codigo_departamento  codigo_entidad  \
0          2016                    5            5000   
1          2016                    8            8000   
2          2016                   11           11001   
3          2016                   13           13000   
4          2016                   15           15000   
..          ...                  ...             ...   
127        2019                   91           91000   
128        2019                   94           94000   
129        2019                   95           95000   
130        2019                   97           97000   
131        2019                   99           99000   

indicador  promedio_del_componente_de_gestion_por_departamento_y_nacion  \
0                                                      53.58              
1                                                      43.68              
2                                                        NaN              
3                                                      38.87              
4                                                      49.53              
..                                                       ...              
127                                                      NaN              
128                                                      NaN              
129                                                      NaN              
130                                                      NaN              
131                                                      NaN              

indicador  promedio_del_componente_de_resultados_por_departamento_y_nacion  \
0                                                      69.22                 
1                                                      69.85                 
2                                                        NaN                 
3                                                      64.78                 
4                                                      67.63                 
..                                                       ...                 
127                                                      NaN                 
128                                                      NaN                 
129                                                      NaN                 
130                                                      NaN                 
131                                                      NaN                 

indicador  participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_actividades_artisticas;_de_entrenamiento_y_otros_servicios_(actividades_artisticas;_de_entretenimiento_y_recreacion_y_otras_actividades_de_servicios;_actividades_de_los_hogares_individuales_en_calidad_de_empleadores;_actividades_no_diferenciadas_de_los_hogares_individuales_como_productores_de_bienes_y_servicios_para_uso_propio)  \
0                                                      14.20                                                                                                                                                                                                                                                                                                                                                                                                          
1                                                       4.58                                                                                                                                                                                                                                                                                                                                                                                                          
2                                                        NaN                                                                

In [166]:
df_vars_modeling_dpto_final = df_vars_modeling_dpto.merge(
    df_investments_dpto.drop(columns=df_investments_dpto.columns[25:]),
    left_on=['anio', 'codigo_departamento'],
    right_on=['anio_corte', 'departame_cod']
).drop(columns=['anio_corte', 'departame_cod','departame_nombre','vacunacion_pentavalente'])

In [167]:
df_vars_modeling_dpto_final

anio  codigo_departamento  codigo_entidad  \
0    2016                    5            5000   
1    2016                    8            8000   
2    2016                   11           11001   
3    2016                   13           13000   
4    2016                   15           15000   
..    ...                  ...             ...   
127  2019                   91           91000   
128  2019                   94           94000   
129  2019                   95           95000   
130  2019                   97           97000   
131  2019                   99           99000   

     promedio_del_componente_de_gestion_por_departamento_y_nacion  \
0                                                53.58              
1                                                43.68              
2                                                  NaN              
3                                                38.87              
4                                                49.53              
..                                                 ...              
127                                                NaN              
128                                                NaN              
129                                                NaN              
130                                                NaN              
131                                                NaN              

     promedio_del_componente_de_resultados_por_departamento_y_nacion  \
0                                                69.22                 
1                                                69.85                 
2                                                  NaN                 
3                                                64.78                 
4                                                67.63                 
..                                                 ...                 
127                                                NaN                 
128                                                NaN                 
129                                                NaN                 
130                                                NaN                 
131                                                NaN                 

     participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_actividades_artisticas;_de_entrenamiento_y_otros_servicios_(actividades_artisticas;_de_entretenimiento_y_recreacion_y_otras_actividades_de_servicios;_actividades_de_los_hogares_individuales_en_calidad_de_empleadores;_actividades_no_diferenciadas_de_los_hogares_individuales_como_productores_de_bienes_y_servicios_para_uso_propio)  \
0                                                14.20                                                                                                                                                                                                                                                                                                                                                                                                          
1                                                 4.58                                                                                                                                                                                                                                                                                                                                                                                                          
2                                                  NaN                                                                                                                                                                                                                                                                                                                     

In [168]:
df_vars_modeling_dpto_final['promedio_del_componente_de_gestion_por_departamento_y_nacion'] = df_vars_modeling_dpto_final['promedio_del_componente_de_gestion_por_departamento_y_nacion']/100
df_vars_modeling_dpto_final['promedio_del_componente_de_resultados_por_departamento_y_nacion'] = df_vars_modeling_dpto_final['promedio_del_componente_de_resultados_por_departamento_y_nacion']/100

In [140]:
df_vars_modeling_dpto_final.to_csv('../../data/df_vars_modeling_dpto_final.csv', index=False)

In [156]:
df_comp_result_dpto_2019 = df_vars_modeling[['anio_corte','codigo_departamento','componente_de_resultados','componente_de_gestion']].groupby(['anio_corte', 'codigo_departamento']).mean().reset_index()[df_vars_modeling[['anio_corte','codigo_departamento','componente_de_resultados','componente_de_gestion']].groupby(['anio_corte', 'codigo_departamento']).mean().reset_index()['anio_corte']==2019].reset_index()
df_comp_result_dpto_2019

index  anio_corte  codigo_departamento  componente_de_resultados  \
0      99        2019                    5                  0.681898   
1     100        2019                    8                  0.693375   
2     101        2019                   11                  0.668040   
3     102        2019                   13                  0.650721   
4     103        2019                   15                  0.689511   
5     104        2019                   17                  0.709732   
6     105        2019                   18                  0.645193   
7     106        2019                   19                  0.636116   
8     107        2019                   20                  0.677230   
9     108        2019                   23                  0.674185   
10    109        2019                   25                  0.668376   
11    110        2019                   27                  0.594381   
12    111        2019                   41                  0.696378   
13    112        2019                   44                  0.636705   
14    113        2019                   47                  0.664840   
15    114        2019                   50                  0.646746   
16    115        2019                   52                  0.672474   
17    116        2019                   54                  0.663604   
18    117        2019                   63                  0.708016   
19    118        2019                   66                  0.703621   
20    119        2019                   68                  0.677482   
21    120        2019                   70                  0.703292   
22    121        2019                   73                  0.672791   
23    122        2019                   76                  0.689526   
24    123        2019                   81                  0.660804   
25    124        2019                   85                  0.655028   
26    125        2019                   86                  0.632686   
27    126        2019                   88                  0.531720   
28    127        2019                   91                  0.636270   
29    128        2019                   94                  0.549040   
30    129        2019                   95                  0.592438   
31    130        2019                   97                  0.525490   
32    131        2019                   99                  0.527402   

    componente_de_gestion  
0                0.586010  
1                0.516175  
2                0.793650  
3                0.390317  
4                0.571896  
5                0.561905  
6                0.526681  
7                0.502752  
8                0.451509  
9                0.477514  
10               0.598974  
11               0.527820  
12               0.580657  
13               0.529659  
14               0.472333  
15               0.572857  
16               0.497604  
17               0.532968  
18               0.619444  
19               0.602108  
20               0.569033  
21               0.412923  
22               0.544412  
23               0.612975  
24               0.555427  
25               0.566796  
26               0.454993  
27               0.590960  
28               0.305530  
29               0.480100  
30               0.503210  
31               0.496997  
32               0.520570

In [169]:
for i in range(len(df_vars_modeling_dpto_final)):
    if df_vars_modeling_dpto_final['anio'].loc[i] == 2019:
        for j in range(len(df_comp_result_dpto_2019)):
            if df_vars_modeling_dpto_final['codigo_departamento'].loc[i] == df_comp_result_dpto_2019['codigo_departamento'].loc[j]:
                df_vars_modeling_dpto_final['promedio_del_componente_de_resultados_por_departamento_y_nacion'].loc[i] = df_comp_result_dpto_2019['componente_de_resultados'].loc[j]
                df_vars_modeling_dpto_final['promedio_del_componente_de_gestion_por_departamento_y_nacion'].loc[i] = df_comp_result_dpto_2019['componente_de_gestion'].loc[j]
df_vars_modeling_dpto_final[df_vars_modeling_dpto_final['anio']==2019]

/usr/local/lib/python3.9/site-packages/pandas/core/indexing.py:1637: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_block(indexer, value, name)


anio  codigo_departamento  codigo_entidad  \
99   2019                    5            5000   
100  2019                    8            8000   
101  2019                   11           11001   
102  2019                   13           13000   
103  2019                   15           15000   
104  2019                   17           17000   
105  2019                   18           18000   
106  2019                   19           19000   
107  2019                   20           20000   
108  2019                   23           23000   
109  2019                   25           25000   
110  2019                   27           27000   
111  2019                   41           41000   
112  2019                   44           44000   
113  2019                   47           47000   
114  2019                   50           50000   
115  2019                   52           52000   
116  2019                   54           54000   
117  2019                   63           63000   
118  2019                   66           66000   
119  2019                   68           68000   
120  2019                   70           70000   
121  2019                   73           73000   
122  2019                   76           76000   
123  2019                   81           81000   
124  2019                   85           85000   
125  2019                   86           86000   
126  2019                   88           88000   
127  2019                   91           91000   
128  2019                   94           94000   
129  2019                   95           95000   
130  2019                   97           97000   
131  2019                   99           99000   

     promedio_del_componente_de_gestion_por_departamento_y_nacion  \
99                                            0.586010              
100                                           0.516175              
101                                           0.793650              
102                                           0.390317              
103                                           0.571896              
104                                           0.561905              
105                                           0.526681              
106                                           0.502752              
107                                           0.451509              
108                                           0.477514              
109                                           0.598974              
110                                           0.527820              
111                                           0.580657              
112                                           0.529659              
113                                           0.472333              
114                                           0.572857              
115                                           0.497604              
116                                           0.532968              
117                                           0.619444              
118                                           0.602108              
119                                           0.569033              
120                                           0.412923              
121                                           0.544412              
122                                           0.612975              
123                                           0.555427              
124                                           0.566796              
125                                           0.454993              
126                                           0.590960              
127                                           0.305530              
128                                           0.480100              
129                                           0.503210              
130                                           0.496997              
131                        

In [170]:
df_vars_modeling_dpto_final[df_vars_modeling_dpto_final['promedio_del_componente_de_gestion_por_departamento_y_nacion'].isna()]

anio  codigo_departamento  codigo_entidad  \
2   2016                   11           11001   
35  2017                   11           11001   
68  2018                   11           11001   

    promedio_del_componente_de_gestion_por_departamento_y_nacion  \
2                                                 NaN              
35                                                NaN              
68                                                NaN              

    promedio_del_componente_de_resultados_por_departamento_y_nacion  \
2                                                 NaN                 
35                                                NaN                 
68                                                NaN                 

    participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_actividades_artisticas;_de_entrenamiento_y_otros_servicios_(actividades_artisticas;_de_entretenimiento_y_recreacion_y_otras_actividades_de_servicios;_actividades_de_los_hogares_individuales_en_calidad_de_empleadores;_actividades_no_diferenciadas_de_los_hogares_individuales_como_productores_de_bienes_y_servicios_para_uso_propio)  \
2                                                 NaN                                                                                                                                                                                                                                                                                                                                                                                                          
35                                                NaN                                                                                                                                                                                                                                                                                                                                                                                                          
68                                                NaN                                                                                                                                                                                                                                                                                                                                                                                                          

    pib_per_capita  pib_per_capita_como_porcentaje_del_promedio_nacional  \
2              NaN                                                NaN      
35             NaN                                                NaN      
68             NaN                                                NaN      

    pib_por_actividades_economicas_-_agricultura;_ganaderia;_caza;_silvicultura_y_pesca_(agricultura;_ganaderia;_caza;_silvicultura_y_pesca)  \
2                                                 NaN                                                                                          
35                                                NaN                                                                                          
68                                                NaN                                                                                          

    pib_por_actividades_economicas_-_explotacion_de_minas_y_canteras_(explotacion_de_minas_y_canteras)  \
2                                                 NaN                                                    
35                                                NaN                                                    
68                                                NaN                                                    

    porcentaje_del_pib_por_actividades_economicas_-_actividades_artisticas;_de_entrenamiento_y_otros_servicios_(actividades_artisticas;_de_entretenim

In [171]:
for i in range(len(df_vars_modeling_dpto_final)):
    if df_vars_modeling_dpto_final['codigo_departamento'].loc[i] == 11:
        for j in range(len(df_vars_modeling)):
            if df_vars_modeling_dpto_final['anio'].loc[i] == df_vars_modeling['anio_corte'].loc[j]:
                df_vars_modeling_dpto_final['promedio_del_componente_de_resultados_por_departamento_y_nacion'].loc[i] = df_vars_modeling['componente_de_resultados'].loc[j]
                df_vars_modeling_dpto_final['promedio_del_componente_de_gestion_por_departamento_y_nacion'].loc[i] = df_vars_modeling['componente_de_gestion'].loc[j]

df_vars_modeling_dpto_final[df_vars_modeling_dpto_final['codigo_departamento']==11]

/usr/local/lib/python3.9/site-packages/pandas/core/indexing.py:1637: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_block(indexer, value, name)


anio  codigo_departamento  codigo_entidad  \
2    2016                   11           11001   
35   2017                   11           11001   
68   2018                   11           11001   
101  2019                   11           11001   

     promedio_del_componente_de_gestion_por_departamento_y_nacion  \
2                                              0.41280              
35                                             0.26410              
68                                             0.32080              
101                                            0.43484              

     promedio_del_componente_de_resultados_por_departamento_y_nacion  \
2                                              0.53240                 
35                                             0.52430                 
68                                             0.50430                 
101                                            0.43611                 

     participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_actividades_artisticas;_de_entrenamiento_y_otros_servicios_(actividades_artisticas;_de_entretenimiento_y_recreacion_y_otras_actividades_de_servicios;_actividades_de_los_hogares_individuales_en_calidad_de_empleadores;_actividades_no_diferenciadas_de_los_hogares_individuales_como_productores_de_bienes_y_servicios_para_uso_propio)  \
2                                                  NaN                                                                                                                                                                                                                                                                                                                                                                                                          
35                                                 NaN                                                                                                                                                                                                                                                                                                                                                                                                          
68                                                 NaN                                                                                                                                                                                                                                                                                                                                                                                                          
101                                                NaN                                                                                                                                                                                                                                                                                                                                                                                                          

     pib_per_capita  pib_per_capita_como_porcentaje_del_promedio_nacional  \
2               NaN                                                NaN      
35              NaN                                                NaN      
68              NaN                                                NaN      
101             NaN                                                NaN      

     pib_por_actividades_economicas_-_agricultura;_ganaderia;_caza;_silvicultura_y_pesca_(agricultura;_ganaderia;_caza;_silvicultura_y_pesca)  \
2                                                  NaN                                                                                          
35                                                 NaN                                                                       

In [184]:
df_vars_modeling_dpto_final.describe()

anio  codigo_departamento  codigo_entidad  \
count   132.000000           132.000000      132.000000   
mean   2017.500000            52.151515    52151.545455   
std       1.122293            30.908010    30907.969832   
min    2016.000000             5.000000     5000.000000   
25%    2016.750000            20.000000    20000.000000   
50%    2017.500000            52.000000    52000.000000   
75%    2018.250000            81.000000    81000.000000   
max    2019.000000            99.000000    99000.000000   

       promedio_del_componente_de_gestion_por_departamento_y_nacion  \
count                                         132.000000              
mean                                            0.479865              
std                                             0.068403              
min                                             0.264100              
25%                                             0.435975              
50%                                             0.481000              
75%                                             0.529390              
max                                             0.619444              

       promedio_del_componente_de_resultados_por_departamento_y_nacion  \
count                                         132.000000                 
mean                                            0.649744                 
std                                             0.050630                 
min                                             0.436110                 
25%                                             0.633350                 
50%                                             0.662852                 
75%                                             0.682199                 
max                                             0.725700                 

       participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_actividades_artisticas;_de_entrenamiento_y_otros_servicios_(actividades_artisticas;_de_entretenimiento_y_recreacion_y_otras_actividades_de_servicios;_actividades_de_los_hogares_individuales_en_calidad_de_empleadores;_actividades_no_diferenciadas_de_los_hogares_individuales_como_productores_de_bienes_y_servicios_para_uso_propio)  \
count                                          96.000000                                                                                                                                                                                                                                                                                                                                                                                                          
mean                                            1.779271                                                                                                                                                                                                                                                                                                                                                                                                          
std                                             2.838261                                                                                                                                                                                                                                                                                                                                                                                                          
min                                             0.010000                                                                                                                                                                                                                                                                                                                           

In [183]:
df_vars_modeling_dpto_final = df_vars_modeling_dpto_final.merge(
    df_vars_modeling[['anio_corte','codigo_departamento','inversion','inversion_conectividad','inversion_transformacion']].groupby(['anio_corte','codigo_departamento']).sum().reset_index(),
    left_on=['anio','codigo_departamento'],
    right_on=['anio_corte','codigo_departamento']
)

In [186]:
df_vars_modeling_dpto_final['inversion_total'] = df_vars_modeling_dpto_final['inversion']
df_vars_modeling_dpto_final['conectividad'] = df_vars_modeling_dpto_final['inversion_conectividad']
df_vars_modeling_dpto_final['transformacion'] = df_vars_modeling_dpto_final['inversion_transformacion']
df_vars_modeling_dpto_final = df_vars_modeling_dpto_final.drop(columns=['inversion_total','inversion_conectividad','inversion_transformacion','anio_corte'])
df_vars_modeling_dpto_final.describe()

anio  codigo_departamento  codigo_entidad  \
count   132.000000           132.000000      132.000000   
mean   2017.500000            52.151515    52151.545455   
std       1.122293            30.908010    30907.969832   
min    2016.000000             5.000000     5000.000000   
25%    2016.750000            20.000000    20000.000000   
50%    2017.500000            52.000000    52000.000000   
75%    2018.250000            81.000000    81000.000000   
max    2019.000000            99.000000    99000.000000   

       promedio_del_componente_de_gestion_por_departamento_y_nacion  \
count                                         132.000000              
mean                                            0.479865              
std                                             0.068403              
min                                             0.264100              
25%                                             0.435975              
50%                                             0.481000              
75%                                             0.529390              
max                                             0.619444              

       promedio_del_componente_de_resultados_por_departamento_y_nacion  \
count                                         132.000000                 
mean                                            0.649744                 
std                                             0.050630                 
min                                             0.436110                 
25%                                             0.633350                 
50%                                             0.662852                 
75%                                             0.682199                 
max                                             0.725700                 

       participacion_de_las_actividades_economicas_del_pib_departamental_en_las_actividades_economicas_del_nacional_-_actividades_artisticas;_de_entrenamiento_y_otros_servicios_(actividades_artisticas;_de_entretenimiento_y_recreacion_y_otras_actividades_de_servicios;_actividades_de_los_hogares_individuales_en_calidad_de_empleadores;_actividades_no_diferenciadas_de_los_hogares_individuales_como_productores_de_bienes_y_servicios_para_uso_propio)  \
count                                          96.000000                                                                                                                                                                                                                                                                                                                                                                                                          
mean                                            1.779271                                                                                                                                                                                                                                                                                                                                                                                                          
std                                             2.838261                                                                                                                                                                                                                                                                                                                                                                                                          
min                                             0.010000                                                                                                                                                                                                                                                                                                                           

In [189]:
df_vars_modeling_dpto_final.describe().transpose()[df_vars_modeling_dpto_final.describe().transpose()['count']<99]

count          mean  \
participacion_de_las_actividades_economicas_del...   96.0  1.779271e+00   
pib_per_capita                                       96.0  1.440647e+07   
pib_per_capita_como_porcentaje_del_promedio_nac...   96.0  9.697625e+01   
pib_por_actividades_economicas_-_agricultura;_g...   96.0  1.846109e+03   
pib_por_actividades_economicas_-_explotacion_de...   96.0  1.489342e+03   
porcentaje_del_pib_por_actividades_economicas_-...   96.0  1.598958e+00   
porcentaje_del_pib_por_actividades_economicas_-...   96.0  2.230208e+00   
porcentaje_del_pib_por_actividades_economicas_-...   96.0  5.491667e+00   
porcentaje_del_pib_por_actividades_economicas_-...   96.0  3.823438e+00   
porcentaje_del_pib_por_actividades_economicas_-...   96.0  2.136062e+01   
porcentaje_del_pib_por_actividades_economicas_-...   96.0  1.154438e+01   
porcentaje_del_pib_por_actividades_economicas_-...   96.0  1.858698e+01   
porcentaje_del_pib_por_actividades_economicas_-...   96.0  8.293750e+00   
porcentaje_del_pib_por_actividades_economicas_-...   96.0  2.592813e+00   
porcentaje_del_pib_por_actividades_economicas_-...   96.0  9.521979e+00   
porcentaje_del_pib_por_actividades_economicas_-...   96.0  6.198437e+00   
porcentaje_del_pib_por_actividades_economicas_-...   96.0  7.051667e+00   
porcentaje_del_pib_por_actividades_economicas_-...   96.0  1.704583e+00   
cobertura_en_educacion_superior                      96.0  3.273385e+01   
mortalidad_en_menores_de_5_anios_por_infeccion_...   98.0  1.848010e+01   
porcentaje_de_nacidos_vivos_hijos_de_mujeres_me...   97.0  2.793814e-01   

                                                             std         min  \
participacion_de_las_actividades_economicas_del...  2.838261e+00        0.01   
pib_per_capita                                      7.247999e+06  5684151.50   
pib_per_capita_como_porcentaje_del_promedio_nac...  4.824524e+01       39.51   
pib_por_actividades_economicas_-_agricultura;_g...  1.972953e+03       17.24   
pib_por_actividades_economicas_-_explotacion_de...  2.983927e+03        0.89   
porcentaje_del_pib_por_actividades_economicas_-...  8.105430e-01        0.33   
porcentaje_del_pib_por_actividades_economicas_-...  8.275747e-01        0.93   
porcentaje_del_pib_por_actividades_economicas_-...  2.224904e+00        1.66   
porcentaje_del_pib_por_actividades_economicas_-...  2.848212e+00        0.09   
porcentaje_del_pib_por_actividades_economicas_-...  9.814048e+00        7.47   
porcentaje_del_pib_por_actividades_economicas_-...  6.501605e+00        0.97   
porcentaje_del_pib_por_actividades_economicas_-...  8.042390e+00       10.19   
porcentaje_del_pib_por_actividades_economicas_-...  2.823817e+00        2.27   
porcentaje_del_pib_por_actividades_economicas_-...  1.764300e+00        0.22   
porcentaje_del_pib_por_actividades_economicas_-...  1.525690e+01        0.09   
porcentaje_del_pib_por_actividades_economicas_-...  3.143206e+00        2.28   
porcentaje_del_pib_por_actividades_economicas_-...  6.285449e+00        0.15   
porcentaje_del_pib_por_actividades_economicas_-...  9.006394e-01        0.09   
cobertura_en_educacion_superior                     1.747785e+01        3.51   
mortalidad_en_menores_de_5_anios_por_infeccion_...  1.288998e+01        0.00   
porcentaje_de_nacidos_vivos_hijos_de_mujeres_me...  1.886731e-01        0.00   

                                                             25%  \
participacion_de_las_actividades_economicas_del...  2.075000e-01   
pib_per_capita                                      8.799540e+06   
pib_per_capita_como_porcentaje_del_promedio_nac...  5.982250e+01   
pib_por_actividades_economicas_-_agricultura;_g...  4.277050e+02   
pib_por_actividades_economicas_-_explotacion_de...  3.391750e+01   
porcentaje_del_pib_por_actividades_economicas_-...  8.975000e-01   
porcentaje_del_pib_por_actividades_economicas_-...  1.547500e+00   
porcentaje_del_pib_por_actividades_economicas_-...  3.962500e+00   
porcentaje_del_pib_por_activ